In [8]:
!pip install pandas numpy scipy plotly
!pip install --upgrade nbformat plotly ipykernel
!pip install dash pandas


[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: python3 -m pip install --upgrade pip

[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: python3 -m pip install --upgrade pip
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.9/7.9 MB 51.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9/9 [dash]8/9 [dash]]ug]

[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: python3 -m pip install --upgrade pip


In [16]:
import pandas as pd
import numpy as np
from scipy import stats
import plotly.express as px
import os

In [3]:

# --- 1. Load the Dataset ---
# Load the CSV file into a pandas DataFrame.
try:
    df = pd.read_csv('fpkm_counts_with_annotations.csv')
    print("File loaded successfully!")
except FileNotFoundError:
    print("Error: 'fpkm_counts_with_annotations.csv' not found.")
    print("Please make sure the CSV file is in the same directory as your notebook.")
    # Stop execution if the file is not found
    exit()


# --- 2. Define Sample Groups ---
# Group the sample columns for easy comparison.
groups = {
    'EBY': ['EBY_1', 'EBY_2', 'EBY_3'],
    'GNSR': ['EBY-GNSR_1', 'EBY-GNSR_2'],
    'GNHR': ['EBY-GNHR_1', 'EBY-GNHR_2', 'EBY-GNHR_3'],
    'GNUR': ['EBY-GNUR_1', 'EBY-GNUR_2', 'EBY-GNUR_3']
}


# --- 3. Define a Function for Differential Expression Analysis ---
def calculate_differential_expression(df, group1_name, group2_name):
    """
    Calculates log2 fold change and p-value for a comparison between two groups.
    """
    group1_cols = groups[group1_name]
    group2_cols = groups[group2_name]

    # Use a small pseudo-count to avoid errors with log(0) or division by zero.
    pseudo_count = 1e-4
    
    # Calculate the mean for each group
    mean_group1 = df[group1_cols].mean(axis=1) + pseudo_count
    mean_group2 = df[group2_cols].mean(axis=1) + pseudo_count

    # Calculate log2 fold change
    log2_fold_change = np.log2(mean_group1 / mean_group2)

    # Perform an independent t-test to get the p-value
    t_stat, p_value = stats.ttest_ind(
        df[group1_cols], df[group2_cols], axis=1, equal_var=False, nan_policy='omit'
    )

    # Create a results DataFrame
    result_df = pd.DataFrame({
        'Geneid': df['Geneid'],
        'log2FoldChange': log2_fold_change,
        'pvalue': p_value
    })
    
    # Calculate -log10(pvalue) and handle p-values of 0
    result_df['-log10(pvalue)'] = -np.log10(result_df['pvalue'].replace(0, 1e-300))
    result_df['comparison'] = f'{group1_name} / {group2_name}'
    
    return result_df


# --- 4. Prepare Data for the Plots ---

# Define the comparisons needed for each plot
plot1_comparisons = [('GNSR', 'EBY'), ('GNUR', 'EBY'), ('GNHR', 'EBY')]
plot2_comparisons = [('EBY', 'GNHR'), ('GNSR', 'GNHR'), ('GNUR', 'GNHR')]

# Calculate results and concatenate them into a single DataFrame for each plot
plot1_df = pd.concat([calculate_differential_expression(df, g1, g2) for g1, g2 in plot1_comparisons])
plot2_df = pd.concat([calculate_differential_expression(df, g1, g2) for g1, g2 in plot2_comparisons])


# --- 5. Generate and Display the Interactive Plots ---

# Plot 1: GNSR/EBY, GNUR/EBY, GNHR/EBY
print("\n--- Generating Plot 1: Comparisons vs. EBY ---")
fig1 = px.scatter(
    plot1_df,
    x='log2FoldChange',
    y='-log10(pvalue)',
    color='comparison',  # Color points by the comparison group
    hover_name='Geneid', # Display Geneid on hover
    title='Volcano Plot: GNSR, GNUR, GNHR vs. EBY',
    labels={
        "log2FoldChange": "log2 Fold Change",
        "-log10(pvalue)": "-log10(p-value)"
    }
)

# Add lines for significance thresholds
fig1.add_hline(y=-np.log10(0.05), line_dash="dash", line_color="grey", annotation_text="p=0.05")
fig1.add_vline(x=1, line_dash="dash", line_color="grey", annotation_text="FC=2")
fig1.add_vline(x=-1, line_dash="dash", line_color="grey")

fig1.show()


# Plot 2: EBY/GNHR, GNSR/GNHR, GNUR/GNHR
print("\n--- Generating Plot 2: Comparisons vs. GNHR ---")
fig2 = px.scatter(
    plot2_df,
    x='log2FoldChange',
    y='-log10(pvalue)',
    color='comparison',
    hover_name='Geneid',
    title='Volcano Plot: EBY, GNSR, GNUR vs. GNHR',
    labels={
        "log2FoldChange": "log2 Fold Change",
        "-log10(pvalue)": "-log10(p-value)"
    }
)

# Add lines for significance thresholds
fig2.add_hline(y=-np.log10(0.05), line_dash="dash", line_color="grey", annotation_text="p=0.05")
fig2.add_vline(x=1, line_dash="dash", line_color="grey", annotation_text="FC=2")
fig2.add_vline(x=-1, line_dash="dash", line_color="grey")

fig2.show()


# --- NEW: Plot 3: GNSR vs. GNUR ---
print("\n--- Generating Plot 3: GNSR vs. GNUR ---")

# First, calculate the data for the new comparison
plot3_df = calculate_differential_expression(df, 'GNSR', 'GNUR')

# Next, create the scatter plot
fig3 = px.scatter(
    plot3_df,
    x='log2FoldChange',
    y='-log10(pvalue)',
    hover_name='Geneid',
    title='Volcano Plot: GNSR vs. GNUR',
    labels={
        "log2FoldChange": "log2 Fold Change",
        "-log10(pvalue)": "-log10(p-value)"
    }
)

# Add lines for significance thresholds
fig3.add_hline(y=-np.log10(0.05), line_dash="dash", line_color="grey", annotation_text="p=0.05")
fig3.add_vline(x=1, line_dash="dash", line_color="grey", annotation_text="FC=2")
fig3.add_vline(x=-1, line_dash="dash", line_color="grey")

fig3.show()

File loaded successfully!

--- Generating Plot 1: Comparisons vs. EBY ---


/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, axis=axis, **kwds)
/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  res = hypotest_fun_out(*samples, axis=axis, **kwds)



--- Generating Plot 2: Comparisons vs. GNHR ---



--- Generating Plot 3: GNSR vs. GNUR ---


/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.



In [4]:
# --- 1. Load and Clean the Dataset ---
try:
    # FIX 1: Using the correct file name provided during upload.
    df = pd.read_csv('fpkm_counts_with_annotations.csv')
    
    # FIX 2: Clean up column names to prevent KeyErrors from hidden whitespace.
    df.columns = df.columns.str.strip()
    
    print("File loaded successfully!")
    print("Columns found:", df.columns.tolist()) # This helps confirm columns are read correctly
    
except FileNotFoundError:
    print("Error: 'fpkm_counts_with_annotations (1).csv' not found.")
    print("Please make sure the CSV file is in the same directory as your notebook.")
    exit()


# --- 2. Define Sample Groups ---
groups = {
    'EBY': ['EBY_1', 'EBY_2', 'EBY_3'],
    'GNSR': ['EBY-GNSR_1', 'EBY-GNSR_2'],
    'GNHR': ['EBY-GNHR_1', 'EBY-GNHR_2', 'EBY-GNHR_3'],
    'GNUR': ['EBY-GNUR_1', 'EBY-GNUR_2', 'EBY-GNUR_3']
}


# --- 3. Define a Function for Differential Expression Analysis ---
def calculate_differential_expression(df, group1_name, group2_name):
    group1_cols = groups[group1_name]
    group2_cols = groups[group2_name]
    pseudo_count = 1e-4
    
    mean_group1 = df[group1_cols].mean(axis=1) + pseudo_count
    mean_group2 = df[group2_cols].mean(axis=1) + pseudo_count
    log2_fold_change = np.log2(mean_group1 / mean_group2)

    t_stat, p_value = stats.ttest_ind(
        df[group1_cols], df[group2_cols], axis=1, equal_var=False, nan_policy='omit'
    )

    result_df = pd.DataFrame({
        'Geneid': df['Geneid'],
        'log2FoldChange': log2_fold_change,
        'pvalue': p_value,
        'comparison': f'{group1_name} / {group2_name}'
    })
    
    # Add -log10(pvalue) for plotting
    result_df['-log10(pvalue)'] = -np.log10(result_df['pvalue'].replace(0, 1e-300))
    
    return result_df


# --- 4. Prepare Data ---
plot1_comparisons = [('GNSR', 'EBY'), ('GNUR', 'EBY'), ('GNHR', 'EBY')]
plot2_comparisons = [('EBY', 'GNHR'), ('GNSR', 'GNHR'), ('GNUR', 'GNHR')]
plot3_comparison = ('GNSR', 'GNUR')

plot1_df = pd.concat([calculate_differential_expression(df, g1, g2) for g1, g2 in plot1_comparisons])
plot2_df = pd.concat([calculate_differential_expression(df, g1, g2) for g1, g2 in plot2_comparisons])
plot3_df = calculate_differential_expression(df, plot3_comparison[0], plot3_comparison[1])


# --- 5. Generate and Display the Interactive Plots (Optional) ---
# You can keep this section if you still want to see the volcano plots.

# --- 6. Filter, Format, and Save Top 5 Genes to a File ---

# Merge annotations for all three comparison sets
annotations_df = df[['Geneid', 'JGI_annotation', 'KEGG_annotation']].copy()
plot1_annotated_df = pd.merge(plot1_df, annotations_df, on='Geneid', how='left')
plot2_annotated_df = pd.merge(plot2_df, annotations_df, on='Geneid', how='left')
plot3_annotated_df = pd.merge(plot3_df, annotations_df, on='Geneid', how='left')

output_filename = "top5_significant_genes_report.txt"

with open(output_filename, 'w') as f:

    def analyze_and_write_results(result_df, title, file_handle):
        file_handle.write("="*80 + "\n")
        file_handle.write(f"Analysis: {title}\n")
        file_handle.write("Filtering for TOP 5 Statistically Significant Genes\n")
        file_handle.write("Conditions: |log2 Fold Change| > 5 AND p-value < 0.05\n")
        file_handle.write("="*80 + "\n\n")

        comparisons = result_df['comparison'].unique()
        
        for comp in comparisons:
            file_handle.write(f"--- Comparison Group: {comp} ---\n")
            
            comparison_df = result_df[result_df['comparison'] == comp]
            
            # --- UPDATED LOGIC ---
            
            # 1. Filter for UPREGULATED genes (p-value < 0.05)
            upregulated_condition = (comparison_df['log2FoldChange'] > 5) & (comparison_df['pvalue'] < 0.05)
            top_5_upregulated = comparison_df[upregulated_condition].sort_values(by='log2FoldChange', ascending=False).head(5)

            # 2. Filter for DOWNREGULATED genes (p-value < 0.05)
            downregulated_condition = (comparison_df['log2FoldChange'] < -5) & (comparison_df['pvalue'] < 0.05)
            top_5_downregulated = comparison_df[downregulated_condition].sort_values(by='log2FoldChange', ascending=True).head(5)

            # Write the upregulated list
            file_handle.write("\n  Top 5 Most Upregulated (Significant):\n")
            if top_5_upregulated.empty:
                file_handle.write("    - None found meeting the criteria.\n")
            else:
                for index, row in top_5_upregulated.iterrows():
                    f.write(f"    Gene: {row['Geneid']} (log2FC: {row['log2FoldChange']:.2f})\n")
                    f.write(f"      - p-value: {row['pvalue']:.4f}\n")
                    f.write(f"      - JGI Annotation: {row['JGI_annotation']}\n")
                    f.write(f"      - KEGG Annotation: {row['KEGG_annotation']}\n")

            # Write the downregulated list
            file_handle.write("\n  Top 5 Most Downregulated (Significant):\n")
            if top_5_downregulated.empty:
                file_handle.write("    - None found meeting the criteria.\n\n")
            else:
                for index, row in top_5_downregulated.iterrows():
                    f.write(f"    Gene: {row['Geneid']} (log2FC: {row['log2FoldChange']:.2f})\n")
                    f.write(f"      - p-value: {row['pvalue']:.4f}\n")
                    f.write(f"      - JGI Annotation: {row['JGI_annotation']}\n")
                    f.write(f"      - KEGG Annotation: {row['KEGG_annotation']}\n")
            
            file_handle.write("\n")

    # Run the analysis for all three sets of comparisons
    analyze_and_write_results(plot1_annotated_df, "Comparisons vs. EBY", f)
    f.write("\n\n")
    analyze_and_write_results(plot2_annotated_df, "Comparisons vs. GNHR", f)
    f.write("\n\n")
    analyze_and_write_results(plot3_annotated_df, "Comparison: GNSR vs. GNUR", f)

# --- 7. Final Confirmation ---
print(f"✅ Report successfully generated and saved to '{output_filename}'")

File loaded successfully!
Columns found: ['Geneid', 'EBY_1', 'EBY_2', 'EBY_3', 'EBY-U_1', 'EBY-GNSR_1', 'EBY-GNSR_2', 'EBY-GNHR_1', 'EBY-GNHR_2', 'EBY-GNHR_3', 'EBY-GNUR_1', 'EBY-GNUR_2', 'EBY-GNUR_3', 'JGI_annotation', 'KEGG_annotation']


/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.

/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.

/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.



✅ Report successfully generated and saved to 'top5_significant_genes_report.txt'


In [7]:
# --- 1. Load the Dataset ---
try:
    df = pd.read_csv('fpkm_counts_with_annotations.csv')
    print(f"Successfully loaded the dataset. Original number of genes: {len(df)}")
except FileNotFoundError:
    print("Error: 'fpkm_counts_with_annotations.csv' not found.")
    exit()

# --- 2. Filter the Data ---
# Keep rows where at least one of the annotation columns is not empty.
original_count = len(df)
filtered_df = df[~(df['JGI_annotation'].isna() & df['KEGG_annotation'].isna())].copy()
filtered_count = len(filtered_df)
print(f"Number of genes after filtering: {filtered_count}")
print(f"Number of genes removed: {original_count - filtered_count}\n")


# --- 3. Define Sample Groups ---
groups = {
    'EBY': ['EBY_1', 'EBY_2', 'EBY_3'],
    'GNSR': ['EBY-GNSR_1', 'EBY-GNSR_2'],
    'GNHR': ['EBY-GNHR_1', 'EBY-GNHR_2', 'EBY-GNHR_3'],
    'GNUR': ['EBY-GNUR_1', 'EBY-GNUR_2', 'EBY-GNUR_3']
}


# --- 4. Define a Function for Differential Expression Analysis ---
def calculate_differential_expression(df_to_process, group1_name, group2_name):
    """
    Calculates log2 fold change and p-value for a comparison between two groups.
    """
    group1_cols = groups[group1_name]
    group2_cols = groups[group2_name]
    
    pseudo_count = 1e-4
    
    mean_group1 = df_to_process[group1_cols].mean(axis=1) + pseudo_count
    mean_group2 = df_to_process[group2_cols].mean(axis=1) + pseudo_count

    log2_fold_change = np.log2(mean_group1 / mean_group2)

    t_stat, p_value = stats.ttest_ind(
        df_to_process[group1_cols], df_to_process[group2_cols], axis=1, equal_var=False, nan_policy='omit'
    )

    result_df = pd.DataFrame({
        'Geneid': df_to_process['Geneid'],
        'log2FoldChange': log2_fold_change,
        'pvalue': p_value
    })
    
    result_df['-log10(pvalue)'] = -np.log10(result_df['pvalue'].replace(0, 1e-300))
    result_df['comparison'] = f'{group1_name} / {group2_name}'
    
    return result_df


# --- 5. Prepare Data for the Plots using FILTERED data ---

# Define the comparisons for each plot
plot1_comparisons = [('GNSR', 'EBY'), ('GNUR', 'EBY'), ('GNHR', 'EBY')]
plot2_comparisons = [('EBY', 'GNHR'), ('GNSR', 'GNHR'), ('GNUR', 'GNHR')]

# Calculate results for each plot using the filtered_df
plot1_df = pd.concat([calculate_differential_expression(filtered_df, g1, g2) for g1, g2 in plot1_comparisons])
plot2_df = pd.concat([calculate_differential_expression(filtered_df, g1, g2) for g1, g2 in plot2_comparisons])
plot3_df = calculate_differential_expression(filtered_df, 'GNSR', 'GNUR')


# --- 6. Generate and Display the Interactive Plots ---

# Plot 1: Comparisons vs. EBY (Filtered)
print("--- Generating Plot 1: Comparisons vs. EBY (Filtered) ---")
fig1 = px.scatter(
    plot1_df,
    x='log2FoldChange',
    y='-log10(pvalue)',
    color='comparison',
    hover_name='Geneid',
    title='Volcano Plot: GNSR, GNUR, GNHR vs. EBY (Filtered)',
    labels={"log2FoldChange": "log2 Fold Change", "-log10(pvalue)": "-log10(p-value)"}
)
fig1.add_hline(y=-np.log10(0.05), line_dash="dash", line_color="grey", annotation_text="p=0.05")
fig1.add_vline(x=1, line_dash="dash", line_color="grey", annotation_text="FC=2")
fig1.add_vline(x=-1, line_dash="dash", line_color="grey")
fig1.show()

# Plot 2: Comparisons vs. GNHR (Filtered)
print("\n--- Generating Plot 2: Comparisons vs. GNHR (Filtered) ---")
fig2 = px.scatter(
    plot2_df,
    x='log2FoldChange',
    y='-log10(pvalue)',
    color='comparison',
    hover_name='Geneid',
    title='Volcano Plot: EBY, GNSR, GNUR vs. GNHR (Filtered)',
    labels={"log2FoldChange": "log2 Fold Change", "-log10(pvalue)": "-log10(p-value)"}
)
fig2.add_hline(y=-np.log10(0.05), line_dash="dash", line_color="grey", annotation_text="p=0.05")
fig2.add_vline(x=1, line_dash="dash", line_color="grey", annotation_text="FC=2")
fig2.add_vline(x=-1, line_dash="dash", line_color="grey")
fig2.show()

# Plot 3: GNSR vs. GNUR (Filtered)
print("\n--- Generating Plot 3: GNSR vs. GNUR (Filtered) ---")
fig3 = px.scatter(
    plot3_df,
    x='log2FoldChange',
    y='-log10(pvalue)',
    hover_name='Geneid',
    title='Volcano Plot: GNSR vs. GNUR (Filtered)',
    labels={"log2FoldChange": "log2 Fold Change", "-log10(pvalue)": "-log10(p-value)"}
)
fig3.add_hline(y=-np.log10(0.05), line_dash="dash", line_color="grey", annotation_text="p=0.05")
fig3.add_vline(x=1, line_dash="dash", line_color="grey", annotation_text="FC=2")
fig3.add_vline(x=-1, line_dash="dash", line_color="grey")
fig3.show()

Successfully loaded the dataset. Original number of genes: 6575
Number of genes after filtering: 5899
Number of genes removed: 676

--- Generating Plot 1: Comparisons vs. EBY (Filtered) ---


/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.

/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.

/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.




--- Generating Plot 2: Comparisons vs. GNHR (Filtered) ---



--- Generating Plot 3: GNSR vs. GNUR (Filtered) ---


In [14]:
# --- 1. Load the Dataset ---
try:
    df = pd.read_csv('fpkm_counts_with_annotations.csv')
    print("Successfully loaded the dataset.")
except FileNotFoundError:
    print("Error: 'fpkm_counts_with_annotations.csv' not found.")
    print("Please make sure the CSV file is in the same folder as this script.")
    exit()

# --- 2. Filter the Data based on annotations---
filtered_df = df.dropna(subset=['JGI_annotation', 'KEGG_annotation'], how='all').copy()
print(f"Working with {len(filtered_df)} genes that have annotations.")


# --- 3. Define Sample Groups ---
groups = {
    'EBY': ['EBY_1', 'EBY_2', 'EBY_3'],
    'GNSR': ['EBY-GNSR_1', 'EBY-GNSR_2'],
    'GNHR': ['EBY-GNHR_1', 'EBY-GNHR_2', 'EBY-GNHR_3'],
    'GNUR': ['EBY-GNUR_1', 'EBY-GNUR_2', 'EBY-GNUR_3']
}


# --- 4. Define Analysis Function ---
def calculate_differential_expression(df_to_process, group1_name, group2_name):
    group1_cols = groups[group1_name]
    group2_cols = groups[group2_name]
    pseudo_count = 1e-4
    mean_group1 = df_to_process[group1_cols].mean(axis=1) + pseudo_count
    mean_group2 = df_to_process[group2_cols].mean(axis=1) + pseudo_count
    log2_fold_change = np.log2(mean_group1 / mean_group2)
    t_stat, p_value = stats.ttest_ind(
        df_to_process[group1_cols], df_to_process[group2_cols], axis=1, equal_var=False, nan_policy='omit'
    )
    # Handle potential p-values of 0 before log10 transformation
    safe_p_value = np.nan_to_num(p_value, nan=1.0)
    safe_p_value[safe_p_value == 0] = 1e-300

    result_df = pd.DataFrame({
        'Geneid': df_to_process['Geneid'],
        'log2FoldChange': log2_fold_change,
        'pvalue': p_value,
        '-log10(pvalue)': -np.log10(safe_p_value),
        'comparison': f'{group1_name} / {group2_name}'
    })
    return result_df

# --- 5. Calculate Data for All Comparisons ---
plot1_comparisons = [('GNSR', 'EBY'), ('GNUR', 'EBY'), ('GNHR', 'EBY')]
plot2_comparisons = [('EBY', 'GNHR'), ('GNSR', 'GNHR'), ('GNUR', 'GNHR')]
plot3_comparison = [('GNSR', 'GNUR')]

all_comparisons = plot1_comparisons + plot2_comparisons + plot3_comparison
all_results_df = pd.concat([calculate_differential_expression(filtered_df, g1, g2) for g1, g2 in all_comparisons])


# --- 6. Filter for Highly Significant Genes ---
p_val_threshold = 4
log2fc_threshold = 2

upregulated = all_results_df[
    (all_results_df['-log10(pvalue)'] > p_val_threshold) &
    (all_results_df['log2FoldChange'] > log2fc_threshold)
].copy()
upregulated['Regulation'] = 'Upregulated'

downregulated = all_results_df[
    (all_results_df['-log10(pvalue)'] > p_val_threshold) &
    (all_results_df['log2FoldChange'] < -log2fc_threshold)
].copy()
downregulated['Regulation'] = 'Downregulated'

significant_genes_df = pd.concat([upregulated, downregulated]).reset_index(drop=True)

# --- NEW: Merge annotations back into the final results ---
annotations_df = filtered_df[['Geneid', 'JGI_annotation', 'KEGG_annotation']]
final_df = pd.merge(significant_genes_df, annotations_df, on='Geneid', how='left')

# Sort the final dataframe for a clean output
final_df = final_df.sort_values(
    by=['comparison', 'Regulation', 'log2FoldChange'], 
    ascending=[True, True, False]
).reset_index(drop=True)


# --- 7. Display and Save Results ---
print("\n--- Most Significantly Regulated Genes ---")
print(f"Found {len(final_df)} genes matching the criteria.")

output_filename = 'significant_genes_with_annotations.csv'
final_df.to_csv(output_filename, index=False)

print(f"\n✅ Successfully saved the results with annotations to '{output_filename}'")

Successfully loaded the dataset.
Working with 5899 genes that have annotations.

--- Most Significantly Regulated Genes ---
Found 1193 genes matching the criteria.

✅ Successfully saved the results with annotations to 'significant_genes_with_annotations.csv'


/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.

/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.

/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.



In [15]:
# --- 1. Load the Dataset ---
try:
    df = pd.read_csv('fpkm_counts_with_annotations.csv')
    print("Successfully loaded the dataset.")
    print(f"Working with all {len(df)} genes.")
except FileNotFoundError:
    print("Error: 'fpkm_counts_with_annotations.csv' not found.")
    print("Please make sure the CSV file is in the same folder as this script.")
    exit()

# --- 2. Define Sample Groups ---
groups = {
    'EBY': ['EBY_1', 'EBY_2', 'EBY_3'],
    'GNSR': ['EBY-GNSR_1', 'EBY-GNSR_2'],
    'GNHR': ['EBY-GNHR_1', 'EBY-GNHR_2', 'EBY-GNHR_3'],
    'GNUR': ['EBY-GNUR_1', 'EBY-GNUR_2', 'EBY-GNUR_3']
}


# --- 3. Define Analysis Function ---
def calculate_differential_expression(df_to_process, group1_name, group2_name):
    group1_cols = groups[group1_name]
    group2_cols = groups[group2_name]
    pseudo_count = 1e-4
    mean_group1 = df_to_process[group1_cols].mean(axis=1) + pseudo_count
    mean_group2 = df_to_process[group2_cols].mean(axis=1) + pseudo_count
    log2_fold_change = np.log2(mean_group1 / mean_group2)
    t_stat, p_value = stats.ttest_ind(
        df_to_process[group1_cols], df_to_process[group2_cols], axis=1, equal_var=False, nan_policy='omit'
    )
    # Handle potential p-values of 0 before log10 transformation
    safe_p_value = np.nan_to_num(p_value, nan=1.0)
    safe_p_value[safe_p_value == 0] = 1e-300

    result_df = pd.DataFrame({
        'Geneid': df_to_process['Geneid'],
        'log2FoldChange': log2_fold_change,
        'pvalue': p_value,
        '-log10(pvalue)': -np.log10(safe_p_value),
        'comparison': f'{group1_name} / {group2_name}'
    })
    return result_df

# --- 4. Calculate Data for All Comparisons ---
plot1_comparisons = [('GNSR', 'EBY'), ('GNUR', 'EBY'), ('GNHR', 'EBY')]
plot2_comparisons = [('EBY', 'GNHR'), ('GNSR', 'GNHR'), ('GNUR', 'GNHR')]
plot3_comparison = [('GNSR', 'GNUR')]

all_comparisons = plot1_comparisons + plot2_comparisons + plot3_comparison
all_results_df = pd.concat([calculate_differential_expression(df, g1, g2) for g1, g2 in all_comparisons])


# --- 5. Label Gene Regulation Status (Instead of Filtering) ---
p_val_threshold = 4
log2fc_threshold = 2

# Define the conditions for labeling
conditions = [
    (all_results_df['-log10(pvalue)'] > p_val_threshold) & (all_results_df['log2FoldChange'] > log2fc_threshold),
    (all_results_df['-log10(pvalue)'] > p_val_threshold) & (all_results_df['log2FoldChange'] < -log2fc_threshold)
]

# Define the labels for each condition
labels = ['Upregulated', 'Downregulated']

# Apply the labels, with a default value for genes that don't meet the criteria
all_results_df['Regulation'] = np.select(conditions, labels, default='Not Significant')


# --- 6. Merge annotations back into the final results ---
annotations_df = df[['Geneid', 'JGI_annotation', 'KEGG_annotation']]
final_df = pd.merge(all_results_df, annotations_df, on='Geneid', how='left')

# Sort the final dataframe for a clean output
final_df = final_df.sort_values(
    by=['comparison', 'Regulation', 'log2FoldChange'], 
    ascending=[True, True, False]
).reset_index(drop=True)


# --- 7. Display and Save Results ---
print("\n--- Complete List of All Genes with Regulation Status ---")
print(f"Processed {len(final_df)} total gene entries across all comparisons.")

output_filename = 'full_gene_list_with_regulation_status.csv'
final_df.to_csv(output_filename, index=False)

print(f"\n✅ Successfully saved the complete list with annotations to '{output_filename}'")

Successfully loaded the dataset.
Working with all 6575 genes.

--- Complete List of All Genes with Regulation Status ---
Processed 46025 total gene entries across all comparisons.


/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.

/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.

/home/codespace/.local/lib/python3.12/site-packages/scipy/stats/_axis_nan_policy.py:611: RuntimeWarning:

Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.




✅ Successfully saved the complete list with annotations to 'full_gene_list_with_regulation_status.csv'


In [18]:
# --- 1. Configuration & Setup ---
# Significance thresholds
P_VAL_THRESHOLD = 4
LOG2FC_THRESHOLD = 2

# List of the 12 plot comparisons
COMPARISON_PAIRS = [
    ('GNSR / EBY', 'GNUR / EBY'),
    ('GNSR / EBY', 'GNHR / EBY'),
    ('GNUR / EBY', 'GNHR / EBY'),
    ('EBY / GNHR', 'GNSR / GNHR'),
    ('EBY / GNHR', 'GNUR / GNHR'),
    ('GNSR / GNHR', 'GNUR / GNHR'),
    ('GNSR / EBY', 'GNSR / GNUR'),
    ('GNUR / EBY', 'GNSR / GNUR'),
    ('GNHR / EBY', 'GNSR / GNUR'),
    ('EBY / GNHR', 'GNSR / GNUR'),
    ('GNSR / GNHR', 'GNSR / GNUR'),
    ('GNUR / GNHR', 'GNSR / GNUR')
]

# Create a directory to save the plots
output_dir = "comparison_plots_significant_only"
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

# --- 2. Load and Prepare Data ---
try:
    full_gene_list = pd.read_csv('full_gene_list_with_regulation_status.csv')
    significant_genes = pd.read_csv('significant_genes_with_annotations.csv')
    print("Successfully loaded data files.")
except FileNotFoundError as e:
    print(f"Error loading files: {e}")
    print("Please make sure all required CSV files are in the same directory as this script.")
    exit()

# Get a unique list of genes that are significant in at least one experiment
genes_to_plot = significant_genes['Geneid'].unique()

# Pivot the full gene list
data_wide = full_gene_list.pivot(
    index='Geneid',
    columns='comparison',
    values=['log2FoldChange', '-log10(pvalue)']
)

# Filter the wide data to only include genes that are significant somewhere
data_wide_filtered = data_wide[data_wide.index.isin(genes_to_plot)]
print(f"Prepared data for {len(data_wide_filtered)} unique significant genes.")


# --- 3. Plotting Loop ---
print("\nGenerating comparison plots...")
for comp_a, comp_b in COMPARISON_PAIRS:
    print(f"  - Plotting '{comp_a}' vs '{comp_b}'")
    
    # Prepare a dataframe for this specific plot
    plot_data = pd.DataFrame(index=data_wide_filtered.index)
    
    # Calculate the differences for X and Y axes
    plot_data['x_diff_log2fc'] = data_wide_filtered[('log2FoldChange', comp_a)] - data_wide_filtered[('log2FoldChange', comp_b)]
    plot_data['y_diff_pval'] = data_wide_filtered[('-log10(pvalue)', comp_a)] - data_wide_filtered[('-log10(pvalue)', comp_b)]
    
    # Determine significance status for coloring
    is_sig_a = (data_wide_filtered[('-log10(pvalue)', comp_a)] > P_VAL_THRESHOLD) & \
               (abs(data_wide_filtered[('log2FoldChange', comp_a)]) > LOG2FC_THRESHOLD)
               
    is_sig_b = (data_wide_filtered[('-log10(pvalue)', comp_b)] > P_VAL_THRESHOLD) & \
               (abs(data_wide_filtered[('log2FoldChange', comp_b)]) > LOG2FC_THRESHOLD)

    # Assign status based on the boolean checks
    statuses = []
    for sig_a, sig_b in zip(is_sig_a, is_sig_b):
        if sig_a and sig_b:
            statuses.append('Significant in Both')
        elif sig_a:
            statuses.append(f'Significant in {comp_a} Only')
        elif sig_b:
            statuses.append(f'Significant in {comp_b} Only')
        else:
            statuses.append('Not Significant in Either')
            
    plot_data['Status'] = statuses

    # --- NEW: Filter out non-significant genes ---
    plot_data = plot_data[plot_data['Status'] != 'Not Significant in Either']

    # --- Generate the Plot ---
    title = f"Comparison of '{comp_a}' vs '{comp_b}' (Significant Genes Only)"
    fig = px.scatter(
        plot_data,
        x='x_diff_log2fc',
        y='y_diff_pval',
        color='Status',
        hover_name=plot_data.index,
        title=title,
        labels={
            "x_diff_log2fc": f"Difference in log2FoldChange",
            "y_diff_pval": f"Difference in -log10(p-value)",
        }
    )
    
    # Add lines for reference
    fig.add_hline(y=0, line_dash="dash", line_color="grey")
    fig.add_vline(x=0, line_dash="dash", line_color="grey")

    # --- Save the Plot ---
    filename_a = comp_a.replace(' / ', '-')
    filename_b = comp_b.replace(' / ', '-')
    output_path = os.path.join(output_dir, f"{filename_a}_vs_{filename_b}.html")
    
    fig.write_html(output_path)

print(f"\n✅ Success! All 12 plots have been saved to the '{output_dir}' folder.")


Successfully loaded data files.
Prepared data for 623 unique significant genes.

Generating comparison plots...
  - Plotting 'GNSR / EBY' vs 'GNUR / EBY'
  - Plotting 'GNSR / EBY' vs 'GNHR / EBY'
  - Plotting 'GNUR / EBY' vs 'GNHR / EBY'
  - Plotting 'EBY / GNHR' vs 'GNSR / GNHR'
  - Plotting 'EBY / GNHR' vs 'GNUR / GNHR'
  - Plotting 'GNSR / GNHR' vs 'GNUR / GNHR'
  - Plotting 'GNSR / EBY' vs 'GNSR / GNUR'
  - Plotting 'GNUR / EBY' vs 'GNSR / GNUR'
  - Plotting 'GNHR / EBY' vs 'GNSR / GNUR'
  - Plotting 'EBY / GNHR' vs 'GNSR / GNUR'
  - Plotting 'GNSR / GNHR' vs 'GNSR / GNUR'
  - Plotting 'GNUR / GNHR' vs 'GNSR / GNUR'

✅ Success! All 12 plots have been saved to the 'comparison_plots_significant_only' folder.
